In [1]:
%pip install accelerate gradio torch torchvision diffusers git+https://github.com/huggingface/transformers@main

  Cloning https://github.com/huggingface/transformers (to revision main) to /tmp/pip-req-build-ijn9gxtf
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers /tmp/pip-req-build-ijn9gxtf
  Resolved https://github.com/huggingface/transformers to commit 011b15c1c75a575fcaee5a50de02ff316881816a
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.4/261.4 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 25.3/25.3 MB 48.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 59.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 34.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.9/92.9 kB 13.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.7/302.7 kB 36.4 MB/s eta 0:00:0

In [2]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM
import torch
from transformers import pipeline

In [3]:
# chatgpt-gpt4-prompts-bart-large-cnn-samsum
tokenizer = AutoTokenizer.from_pretrained("Kaludi/chatgpt-gpt4-prompts-bart-large-cnn-samsum")
model = AutoModelForSeq2SeqLM.from_pretrained("Kaludi/chatgpt-gpt4-prompts-bart-large-cnn-samsum", from_tf=True)

# zephyr
pipe = pipeline("text-generation", model="HuggingFaceH4/zephyr-7b-alpha", torch_dtype=torch.bfloat16, device_map="auto")

def useZephyr(prompt):
    messages = [
        {
            "role": "system",
            "content": "You are a friendly chatbot who always responds in the style of a pirate.",
        },
        {"role": "user", "content": prompt},
    ]
    # https://huggingface.co/docs/transformers/main/en/chat_templating
    prompt = pipe.tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    print(prompt)

    outputs = pipe(prompt, max_new_tokens=256, do_sample=True, temperature=0.7, top_k=50, top_p=0.95)
    return outputs[0]["generated_text"]

All TF 2.0 model weights were used when initializing BartForConditionalGeneration.

Some weights of BartForConditionalGeneration were not initialized from the TF 2.0 model and are newly initialized: ['model.encoder.embed_tokens.weight', 'model.decoder.embed_tokens.weight', 'lm_head.weight', 'lm_head.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

In [4]:
def generatePrompt(prompt, max_new_tokens):
    batch = tokenizer(prompt, return_tensors="pt")
    generated_ids = model.generate(batch["input_ids"], max_new_tokens=int(max_new_tokens))
    output = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)
    prompt = output[0]

    return useZephyr(prompt)

def generate_test(prompt):
    batch = tokenizer(prompt, return_tensors="pt")
    generated_ids = model.generate(batch["input_ids"], max_new_tokens=150)
    output = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)
    return output[0]

def generate_prompt(prompt, max_new_tokens):
      return generatePrompt(prompt, max_new_tokens)
#

In [5]:
import gradio as gr

input_prompt = gr.Textbox(label = "Prompt", value = "photographer")
input_maxtokens = gr.Textbox(label = "Max tokens", value = "150")
output_component = gr.Textbox(label = "Output")
examples = [["photographer"], ["developer"], ["teacher"], ["human resources staff"], ["recipe for ham croquettes"]]
description = ""
demo = gr.Interface(useZephyr, inputs = [input_prompt,input_maxtokens], outputs=output_component, examples=examples, title = "🗿 PerfectGPT v1 🗿", description=description).launch(share=True)

# demo = gr.Interface(fn=useZephyr, inputs="text", outputs="text")

demo.launch()

Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://dbb2efcc3beb268bb9.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


In [7]:
%pip freeze > requirements.txt